## This week we learned how to implement edit distance, local alignment, global alignment, and assembly (overlaps). 

We learned how to use dynamic programming for both alignment and assembly. Edit distance is defined as the minimum number of substitutions or insertions or deletions required to turn one string into another.

## Write a function to determine the edit distance between the best match of a pattern and reference genome excerpt. 

Modify the editDistnace function for global alignment to perform local alignment. Global alignment would penalize for each base the reference has that the pattern does not have. Local alignment compares substrings of the same size. 

Modifications needed: 
* elements in first row (bases from P) are 0
* edit distance = minimum value in bottom row, instead of just the value in the bottom right corner. 

Dowload reference sequence from: https://d28rh4a8wq0iu5.cloudfront.net/ads1/data/chr1.GRCh38.excerpt.fasta/

In [50]:
# Imports
from collections import defaultdict

In [1]:
def readFasta(filename):
    genome = ''
    with open(filename, 'r') as f:
        for line in f:
            # ignore header line with genome information
            if not line[0] == '>':
                genome += line.rstrip()
    return genome

In [2]:
chromosome_excerpt = readFasta('chr1.GRCh38.excerpt.fasta')

In [ ]:
# global alignment
def editDistance(x, y):
    # Create distance matrix
    D = []
    for i in range(len(x)+1):
        D.append([0]*(len(y)+1))
    # Initialize first row and column of matrix
    for i in range(len(x)+1):
        D[i][0] = i
    for i in range(len(y)+1):
        D[0][i] = i
    # Fill in the rest of the matrix
    for i in range(1, len(x)+1):
        for j in range(1, len(y)+1):
            distHor = D[i][j-1] + 1
            distVer = D[i-1][j] + 1
            if x[i-1] == y[j-1]:
                distDiag = D[i-1][j-1]
            else:
                distDiag = D[i-1][j-1] + 1
            D[i][j] = min(distHor, distVer, distDiag)
    # Edit distance is the value in the bottom right corner of the matrix
    return D[-1][-1]

In [3]:
# Test example
P = 'GCGTATGC'
T = 'TATTGGCTATACGGTT'

In [8]:
#global alignment
editDistance(P,T)

11

In [39]:
# change to local alignment
def editDistanceLocal(x, y):
    # Create distance matrix
    D = []
    for i in range(len(x)+1):
        D.append([0]*(len(y)+1))
    # Initialize first row and column of matrix - all 0's for local
    for i in range(len(x)+1):
        D[i][0] = i
    for i in range(len(y)+1):
        D[0][i] = 0
    # Fill in the rest of the matrix
    for i in range(1, len(x)+1):
        for j in range(1, len(y)+1):
            distHor = D[i][j-1] + 1
            distVer = D[i-1][j] + 1
            if x[i-1] == y[j-1]:
                distDiag = D[i-1][j-1]
            else:
                distDiag = D[i-1][j-1] + 1
            D[i][j] = min(distHor, distVer, distDiag)
    # Edit distance for local alignment = min value in bottom row
    #top_row = D[:][0]  # check
    bottom_row = D[:][-1]
    edit_dist = min(bottom_row)
    return edit_dist

In [40]:
# test example again - local alignment 
editDistanceLocal(P,T)

2

In [41]:
# another example 
p = 'GCTGATCGATCGTACG'
t = chromosome_excerpt

editDistanceLocal(p,t)

3

In [42]:
# example 3
x = 'GATTTACCAGATTGAG'

editDistanceLocal(x,t)

2

## Make an Overlap Graph for only exact matches, k bases long. 

Approach: Instead of going through each possible permutation of pairs, choose a read, take the suffix of that read and search other reads for it. If no other reads contain this sequence, there can be no overlaps with this read. We can ignore this read and move to another. (This only works for exact matching).
    

Download data from: https://d28rh4a8wq0iu5.cloudfront.net/ads1/data/ERR266411_1.for_asm.fastq

Caveat- For simplicity, no 2 reads in this FASTQ file have the same sequences. 

In [43]:
def readFastq(filename):
    sequences = []
    with open(filename) as fh:
        # this goes through each line for the sequence. 
        while True:
            fh.readline() # first line = name; read but don't save
            seq = fh.readline().rstrip() # second line - bases - save to seq
            fh.readline() # skip placeholder line
            fh.readline() #skip base quality line
            if len(seq) == 0:  # checks for end of file
                break
            sequences.append(seq)
    return sequences

In [44]:
seqs = readFastq('ERR266411_1.for_asm.fastq')

In [47]:
print(len(seqs))
print(seqs[0])

10000
TAAACAAGCAGTAGTAATTCCTGCTTTATCAAGATAATTTTTCGACTCATCAGAAATATCCGAAAGTGTTAACTTCTGCGTCATGGAAGCGATAAAACTC


Implementation: 
1. Create a dictionary of k-mers
    * Key will be the k-mer sequence
    * Value will be a set of reads containing the k-mer (sequences of the sets)
2. For each read, find overlaps involving suffix of that read. 
    * Call the overlap function on the read's suffix and all sequences in the read's set of possible overlaps. 
    * Do not call the overlap function on any reads that don't contain the original read's suffix. 

In [70]:
# pick out all kmers from one sequence. save to a list
seq = seqs[0]
kmers = []
kmer_length = 30
for i in range(len(seq)+1): 
    substring = seq[i:i+kmer_length]
    if len(substring) == kmer_length: 
        kmers.append(substring)
print(len(kmers))
print(len(set(kmers)))

71
71


In [72]:
# make a list of all kmers over all reads
all_kmers = []
kmer_length = 30
for s in seqs: 
    #kmers = []
    for i in range(len(s)+1): 
        substring = s[i:i+kmer_length]
        if len(substring) == kmer_length: 
            all_kmers.append(substring)
    #print('seq#: ' + str(s))
    #print(len(kmers))
    #print(len(set(kmers)))
    #all_kmers.append()
print(len(all_kmers))
print(len(set(all_kmers)))

710000
108344


In [73]:
len(set(all_kmers))

108344

In [74]:
# turn the list into a dictionary 
index = defaultdict(set)

ANOTHER APPROACH - dictionary as we go through the reads

In [86]:
kmer_dict = defaultdict(set)
kmer_length = 30
for s in seqs: 
    for i in range(len(s)+1): 
        substring = s[i:i+kmer_length]
        if len(substring) == kmer_length: 
            kmer_dict[substring].add(s)
len(kmer_dict)

108344

In [89]:
for key, value in kmer_dict.items(): 
    print()

defaultdict(set,
            {'TAAACAAGCAGTAGTAATTCCTGCTTTATC': {'AACTTTCTCATTTTCCGCCAGCAGTCCACTTCGATTTAATTCGTAAACAAGCAGTAGTAATTCCTGCTTTATCAAGATAATTTTTCGACTCATCAGAAAT',
              'AAGGATAGGTCGAATTTTCTCATTTTCCGCCAGCAGTCCACTTCGATTTAATTCGTAAACAAGCAGTAGTAATTCCTGCTTTATCAAGATAATTTTTCGA',
              'AATTCGTAAACAAGCAGTAGTAATTCCTGCTTTATCAAGATAATTTTTCGACTCATCAGAAATATCCGAAAGTGTTAACTTCTGCGTCATGGAAGCGATA',
              'AATTTTCTCATTTTCCGCCAGCAGTCCACTTCGATTTAATTCGTAAACAAGCAGTAGTAATTCCTGCTTTATCAAGATAATTTTTCGACTCATCAGAAAT',
              'ACTTCGATTTAATTCGTAAACAAGCAGTAGTAATTCCTGCTTTATCAAGATAATTTTTCGACTCATCAGAAATATCCGAAAGTGTTAACTTCTGCGTCAT',
              'AGCAGTCCACTTCGATTTAATTCGTAAACAAGCAGTAGTAATTCCTGCTTTATCAAGATAATTTTTCGACTCATCAGAAATATCCGAAAGTGTTAACTTC',
              'AGCTGCGCAAGGATAGGTCGAATTTTCTCATTTTCCGCCAGCAGTCCACTTCGATTTAATTCGTAAACAAGCAGTAGTAATTCCTGCTTTATCAAGATAA',
              'AGCTGCGCAAGGATAGGTCGAATTTTCTCATTTTCCGCCAGCAGTCCACTTCTATTTAATTCGTAAACAAGCAGTAGTAATTCCTGCTTTATCAAGATAA',
     

In [97]:
seq

'TAAACAAGCAGTAGTAATTCCTGCTTTATCAAGATAATTTTTCGACTCATCAGAAATATCCGAAAGTGTTAACTTCTGCGTCATGGAAGCGATAAAACTC'

In [102]:
seq[-30:]

'AACTTCTGCGTCATGGAAGCGATAAAACTC'

In [104]:
def overlap(a, b, min_length):
    """ Return length of longest suffix of 'a' matching
        a prefix of 'b' that is at least 'min_length'
        characters long.  If no such overlap exists,
        return 0. """
    start = 0  # start all the way at the left
    while True:
        start = a.find(b[:min_length], start)  # look for b's prefix in a
        if start == -1:  # no more occurrences to right
            return 0
        # found occurrence; check for full suffix/prefix match
        if b.startswith(a[start:]):
            return len(a)-start
        start += 1  # move just past previous match

In [129]:
for s in seqs: 
    print(s[-30:])

AACTTCTGCGTCATGGAAGCGATAAAACTC
CTTCTGCGTCATGGACACGAAAAAACTCCC
CTTCTGCGTCATGGAAGCGATAAAACTCTG
ATTGGCGTATCCAACCTGCAGAGTTTTATC
GCTTCCATGACGCAGAAGTTAACACTTTCG
AATGATTGGCGTATCCAACCTGCAGAGTTT
TTTTATCGCTTCCATGACGCAGAAGTTAAC
TTCCATGACGCAGAAGTTAACACTTTCGGA
TAACTTTTGCGTCATGGAAGCGATAAAACC
TAACTTCTGCGTCATGGAAGCGATAAAACT
AAAAATGATTGGCGTATCCAACCTGCAGAG
ACTTCTGCGTCATGGAAGCGATAAAACTCT
ACAAAAAGAGCGATGAAAATGAGACTCGGA
GAGTTTTATCGCTTCCATGACGCAGAAGTT
TGACGCAGAAGTTAACACTTTCGGATATTT
CATGACGCAGAAGTTAACACTTTCGGATAT
TTAACTTCTGCGTCATGGAAGCGATAAAAC
AGTTTTATCGCTTCCATGACGCAGAAGTTA
CCAACCTGCAGAGTTTTATCGCTTCCATGA
GTTAACTTCTGCGTCATGGAAGCGATAAAA
ATAAAAATGATTGGCGTATCCAACCTGCAG
TCCAACCTGCAGAGTTTTATCGCTTCCATG
CAACCTGCAGAGTTTTATCGCTTCCATGAC
TGTTAACTTCTGCGTCATGGAAGCGATAAA
CTGTAGCCGACGGTTTGGCGGGGCGACCCG
GGGTTAACTTCTGCGTCATGGAAGCGATAA
GACGTTTTGGCGGGGCCACCTGGGACGGCA
GTGTTAACTTCTGCGTCATGGAAGCGATAA
GACGACAAATATTCACAAAATTATGGGCGC
GTGTTAACTTCTGCGTCATGGAAGCGATAA
TTATCGCTTCCATGACGCAGAAGTTAACAC
ATAAAAATGATTAGCGTATCCAACCTCCAG
AGTGTTAA

TATCAAACCTGCAGAGTTTTATCGCTTCCC
AAGGATAGGTCGAATTTTCTCATTTTCCAT
CAAGGATAGGTCGAATTTTCTCATTTTCCG
AACCTGCAGAGTTTTATCGCTTCCATGACG
CAAGGATAGGCCGAAATTTCTCATTTTCCC
TAAAAATGATTGGCGTATCCAACCTGCAGA
GTTAACACTTTCGGATATTTCTGATGAGTC
AAGATAACACTTTCGGATATTTCTGATGAG
CAAGGATAGGACGAATTTTCTCATTTTCCG
CAAGGATAGGGCGAATTTTCTCATTTTCCG
CTGCAGAGATTTATCGCTTCCATGACGCAG
TCCAACCTGCAGAGTTTTATCGCTTCCATG
GAGGTTAACACTTTCGGATTTTTTGGTTAA
GCAAGGATAGGTCGAATTTTATCATTTTCC
GCAAGGATAGGTCGAATTTTCTCATTTTCC
GCAAGGATAGGTTGAATTTTCTCCTTTTCC
GCAAGGATAGGTCGAATTTTCTCATTTTCC
ACCTGCAGAGTTTTATCGCTTCCATGACGC
GACGCAGAAGTTAACACTTTCGGATATTTC
GCAAGGATAGGTCGAATTTTCTCATTTTCC
GCAAGGATAGGTCGAATTTTCTCATTTTCC
TTTACGAATTAAATCGAAGTGGACTGCTGG
GCAAGGATAGGTCGAAATTTCTCATTTTCC
GCAAGGATAGGTCGAATTTTCTCATTTTCC
AGTTAACACTTTCGGCTATTTCTGATGAGT
CAGAGCTTTATCGCTTCCATGACGCAGGAG
GCAAGGAAAGGTCGAATTTTCTCATTTTCC
GCGTATCCAACCTGCAGAGTCTTATGGCTT
CTGCTTGTTTACGAATTAAATCGAAGTGGA
GCCAGGATAGGTCGGATTTTATCATTTTCC
TATCGCTTCCATGACGCAGAAGTTAACACT
TTTTATCGCTTCCATGACGCAGAAGTTAAA
GCAAGGAT

ACAGAATCGTTAGTTGATGGCGAAAGGTCG
CAGAACCGTTAGTTGATGGCGAAAGGTCGC
ACAGAATCGTTAGTTGATGGCGAAAGGGCG
TTTCGGGTATTTCTGATGAGTCGAAAAATT
ACAGAATCGTTAGTTTATGGCGAAAGGTCG
AATCGAAGTGGACTGCTGGCGGAAAATGAG
ACAGAATCGTTAGTTGATGGCGAAAGGCCG
ACAGAATCGTTAGTTCATGGCGAAAGGCCG
GATTCTGTCAAAAACTGACGCGTTGGATGA
AACACTTTCGGATATTTCTGATGAGTCGAA
ATTGGCGTATCCAACCTGCAGGGTTTTATC
ATGACGCAGAAGTTAACACTTTCGGATATT
ACAGAATCGTTAGTTGATGGCGAAAGGTCG
ACAGAATCGTTAGTTGATGGCGAAAGGTCG
ACAGAATCGTTAGTTGATGGCGAAAGGTCG
TTATCGCTTCCATGACGCAGAAGATAACAC
ACAGAATCGTTAGTTGATGGAGAAAGGGGG
ACAGAATCGTTAGTTGATGGCGAAAGTTCG
GACAGAATCGTTAGTTGATGGCGAAAGGTC
GACAGAATCGTTAGTTGATGGCGAAAGGCC
ATGAGAAAATTCGACCTATCCTTGCGCAGC
GACAGAATCGTTAGTTGATGGCGAAAGGGG
ATCTTGATAAAGCAGGAATTACTACAGCTT
GACAGAATCGTTAGTTGATGGCGAAAGGGC
GACAGAATCGTTAGTTGATGGCGAAAGGTG
GACAGAATCGTTAGTTGATGGCGAAAGGAC
TAATTGGAAGGGGCTTGTTGCCGGAAAAGG
TGACAGAATCGTTAGTTGATGGCGAAAGGT
AACACTTTCGGATATTTCTGATGAGTCGAA
TGACAGAATCGTTAGTTGAAGGCGAAAGGT
GACAGAATCGTTAGTTGATGGCGAAAGGTA
TTGACCTATCCTTGCGCAGCTCGAGAAGCT
TGACAGAA

GACGCGTTGGATGAGAAGAAGTGGCTTAAT
CCTATCCTTGCGCAGCTCGAGAAGCTCTTT
CATCAACTAACGATTCTGTCAAAAACTGAC
ATCTAAACCAGTCCTCGACGAACGTGCCAA
TGCGCAGCTCGAGAAGCTCTTACTTTGCGA
ATCTAAACCAGTCCTTGACGAACGTGCCAA
GCAGCTCGAGAAGCTCTTACTTTGCGACCT
TGCTTGCGCAGCTCGAGAAGCCCTTACTTT
ATGAGAAAATTCGACCTATCCTTGCGCAGC
AATTCGACCTATCCTTGCGCAGCTCGAGAA
CCTTGCGCAGCTCGAGAAGCTCTTACTTTA
TATCTAAACCAGTCCTTGACGAACGTGCCA
ACGCCATCAACTAACGATTCTGTCAAAAAC
TAACTAAACCAGTCCTTGGCGAACGTGCCA
GAGAAAATTCGACCTATCCTTGTGCAGCTC
GCTTGTTTACGAATTAAATCGAAGTGGACA
ATTTTAAAAGAGCGTGGATTACTATCTGAG
TCGAAGTGGAATCCTGGCGGAAAATGAGAA
TATCTAAACCAGTCCTTGACGAACGTGCCA
TATCTAAACCAGTCCTTGACGAACGTGCCA
TATCTAAACCAGTCCTTGACGAACGTTCCA
TTACTACTGCTTGCTTACGAATTAAATCGA
TATCTAAACCAGTCCTTGACGAACGTGCCA
ATATCTAAACCAGTCCTTGACGAACGTGCC
AAGCTCTTACTTTGCGACCTTTCGCCCTCA
TTTTAAAAGAGCGTGGATTACTATCTGAGT
ACGCGTTGGATGAGGAGAAGTGGCTTAATA
CGAAGTGGACTGCTGGCGGAAAATGAGCAA
ATATCTAAACCAGTCCATGACGAACGTGCC
TGGATGAGGAGAAGTGGCTTAATATGCTTG
AATTAAATCGAAGTGGACTGCTGGCGGAAA
ATATCTAAACCAGTCCTTGACGAACGTGCC
CCTCACCT

ACTCAGATAGTAATCCCCGCTCTTTTAAAA
ACTCAGATCGTAATCCACGCTCTTTTAAAA
ACTCAGATAGTAATCCACGCTCTTTTAAAA
ACCCAGATAGTAATCCACGCTCTTTTAAAA
ACTAACGATTCTGTCAAAAACTGACGCGTG
CTACCTTTCGCCATCAACTAACGATTCTGT
ACTCAGATAGTAATCCACGCTCTTTTAAAA
CCTCAGATAGTAATCCACGCTCTTTTAAAA
CGTTGGATGAGGAGAAGTGGCTTAATATGC
GAGGAGAAGCGGCTTAATATGCTTGGCACG
GACTCAGATAGTAATCCACGCTCTTTTAAA
GACTCAGATAGAAATCCCCGCTCTTTTAAA
AGTCACATTTTGTTCATGGTAGAGATTCTC
GACTCAGATAGTAATCCACGCTCCTTTAAA
TAGGTAAGAAATCATGAGTCAAGTTACTGA
TTTGCGACCTTTCGCCATCAACTAACGATT
CTTAATATGCTTGGCACGTTCGTCAAGGAC
GACTCAGATAGTAATCCTCGCTCTTTTAAA
TTACTTTGCGACCTTTCTCCATCAACTAAC
GGAGAAGTGGCTTAATATGATTGGCACGTT
AGTGGCTTAATATGCGTGGCACGTTCGTCA
GACTCAGATAGCAATCCACGCTCTTTTAAA
GACTCAGATAGTAATCCACGCTCTTTTAAA
AAAACTGACGCGTTGGATGAGAAGAAGTGG
GCCATCACCTAACGATTCTGTCAAAAACTG
GACTCCGAAAGGAAACCACGCTCTTTTAAA
GATTACTATCTGAGTCCGATGCTGTTCAAC
TCTTACTTTGCGACCTTTCGCCATCAACTA
GACTCAGATAGAAATCCACGCTCTTTTAAA
GGACTCAGATAGTAATCCACGCTCTTTTAA
AGCTCGAGAAGCTCTTACTTTGCGACCTTT
GGACTCAGATAGAAATCCACGCTCTTTTAA
TGCCGCGC

...

TACTCGTCAGAAAATTGAAATCATCTTCGG
CCGTTTTGGATTTAACCGAAGATGATTTCG
TACTCGTCAGAAAATCGAAATCATATTCGG
TACTCGTCAGAAAATCGAAATCATCTTCTG
GCTGTTCAACCACTAAAAGGTAAGAAATCA
TACTCGTCAGAAAATCGAAATCATCTTCGG
TTCAACCACTAATAGGTAAGAAATCATTAA
TACTCGTCAGAAAATCGAAATCATCTTCGG
TACCCGTCAGAAAATCGAAATCATATTCGG
GAGATTCTCTTGTTGACATTTTAAAAGAGC
TTACTCGTCAGAAAATCGAAATAATCTTCG
TTACTCGTCAGAAAATCGAAATCATCTTCG
TTACTCGTCAGAAAATCGAAATCATCTTCG
GAGTCCGATGCTGTTCAACCACTAATAGGT
CCGTTTTGGATTTAACCGAAGATGATTTCG
TTACTCGTCAGAAAATCGAAATCATCTTCG
TTACTCGTCAGAAAATCGAAACCATCTTCG
AAGAAAATCAAAATAATCTTCGCAAAAAAC
ATCATGAGTCAAGTTACTGAACAATCAGTA
TTACTCGTCAGAAAATCGAAATCATCTTCG
GTTCAACCACTAATAGGTAAGAAATCATGA
TTACTCGTCAGAAAATCAAAATCATCTTCG
CTTTTAAAAGAGCGTGGATTACTATATGAG
TTTAACCACTAATAGGTAAGAAATCATGAG
TTACTCGTCAGAAAATCGAAATCATCTTCG
TTACTCGTCAGAAAATCGAAATCATCTTCG
TTACTCGTCAGAAAATCGAAATCATCTTCG
CGTGGATTACTATCTGAGTCCGATGATGTT
CAACCACTAATAGGTAAGAAATCATGAGTC
TTACTCGCCAGAAAATCGAAATCATCTTCG
TTACTCGTCAGAAAATCGAAATCATCTTCG
GTTACTCGTCAGAAAATCGAAATCATCTTC
GTTACTCG

GAGTAACAAAGTTTGGATTGCTACTGACCG
CAAGCCTCAACGCAGCGACGAGCACGAGAG
ATTTTCTGACGAGGAACAAAGTTTGGATTG
CAAGCCTCAACGCAGCGACGAGCACGAGAG
CAAGCCTCAACGCAGCGACGAGCACGAGAG
TCATGAGTCACGTTACTGAACAATCCGTAC
CAAGCCTCAACGCAGCGACGAGCACGAGAG
AAAGCCTCAACGCAGCGACGAGCACGAGAG
ATGCTGTTCAACCACTAATAGGTAAGAAAT
CAAGCCTCAACGCAGGGACGAGCACGAGAG
TTTGGCCTCTATTAAGCTCATTCCGGCATC
CTCGTGCTCGTCGCTGCGTTGAGGCTTGCG
GCTACTGACCGCTCTCGTGCTCGTCGCTGC
CAAGCCTCAACGCAGCGACGAGAACGAGAG
CAAGCCTCAACGCAGCGACGAGCACGAGAG
TGACCGCTCTCGTGCTCGTCGCTGCGTTGA
CGAGCCTCAACGCAGCGACGAGCACGAGAG
TAACAAAGTTTGGATTGCTACTGACCGCTC
CAAGCCTCAACGCAGCGACGAGAACGAGAG
AAGCCTCAACGCAGCGACGAGCACAAGAGC
CAAGCCTCAACGCAGCGACGAGCACGAGAG
CAAGCCACAACGCAGCGACGAGCAAGAGAG
CAAGCCTCAACGCAGCGACGAGCAAGAGAG
TCATGAGTCAAGTTACTAAACAATCCGTAC
CGTACGTTTCCAGACCGCTTTGGCCTCTAT
CAAGCCTCAACGCAGAGACGAGCACGAGAG
CAAGCCTCAACGCAGCGACGAGCACGAGAG
GAGTCAAGTTACTGAACAATCCGTACGTTT
CAAGCCTCAACGCAGCGACGAGCACGAGAG
AAAGCCTCAACGCAGCGACGAGCACGAGAG
CAAGCCTCAACGCAGCGACGAGCCCGAGAG
CAAGCCTCAACGCAGCGACGAGCACGAGAG
GCAAGCCT

TCCAGACCGCCTTGGCCTCTATTAAGCTCA
CGAGGGTATCCTACAAAGTCCAGCGTACCA
CCGAAGATGATTTCGATTTTCTTTCGAGTA
CGAGGGAATCCTACAAAGTCCAGCGTACCA
CGAGGGTATCCTACAAAGTCCAGCGAACCA
GCTTCTGCCGCCTTTGTTTTAATCGAAGAT
CGAGGGTATCCTACAAAGTCCAGCGTACCA
GATGATTTCGATTTTCTGACGAGTCACAAA
TCAAGTTACTGAACAATCCGTACGTTTCCA
CGAGGGCATCCTACAAAGTCCAGCGGACCA
GACTTAACCGAACTTGATTTCGATTTTCTG
TCTCGTGCTCGTCACTGCGTTGAGGCTTGC
CGAGGGTATCCTACAAAGACCAGCGTACCA
CGAGGGTATCCTACAAAGTCCAGCGTACCA
GTTTCCAGACCGCTTTGGCCTCTATTAAGC
CAATCCGTACGTTTCNAGACCGCTTTGGCC
TGGCCTCTCTTAAGCTCATTCAGGCTTCTG
GCGAGGGTATCCTACAAAGTCCCGCGTACC
GCGAGGGTATCCTACAAAGTCCAGCGTACC
GCGAGGGGATCCTACAAAGTCCAGCGTACC
CCTCTATTAAGCTCATTCAGGCTTCTGCCG
ATCCGTACGTTTCCAGACCGCTTTGGCCTC
GCGAGGGTATCCTACAAAGTCCAGCGTACC
GCGAGGGCATCCTACAAAGCCCAGCGTACC
TCGCTTTCCTGCTCCTGTTGCGTTTATTGC
TGCCGTCATTGCTTATTATGTTCATCCCGT
GCGTTTATGGTACGCTGGACTTTGTAGGAT
GCGAGGGGATCCTACAAAGTCCAGCGAACC
GGATCCCACAAAAACCCGCGGACCCCAAAA
GCGAGGGGATCCTACAAAGTCAAGCGTACC
GCGAGGGTATCCTACAAAGTCCAGCGTACA
AGCTCATTCAGGCTTCTGCCGTTTTGGGTT
GCGAGGGA

ATGAACATAATAAGAAATGACGGCAGCAAT
TTATGGTACGCTGGACTTTGTAGGATACCC
TGATTTCGATTTTCTGACGAGTAACAAAGA
ATGAACATAATAAGCAATGACGGCAGAAAT
ATTCAGGCTTCTTCCGTTTTGGATTTAACC
TGACCGCTCTCGTGCTCGTCGCTGCGTTGG
TCGTCGCTGCGTTGAGGCTTGCGGTTATGG
GCTTATTATGTTCATCCCGTCAACATTCAA
ATGAACCTAATAAGCAATGACGGCAGCAAT
ATGAACATAATAAGCAATGACAGCAGCAAT
ATGAACATAATAAGCAATGACGGCAGGAAA
ATGAACATAATAAGCAATGACGGCAGCAAA
ATGAACATAATAAGCAATGACGGCAGCAAA
GCCGTTTTTGATTTGACCGAAGATGATTTC
CGTTTATGGTACGCTGGACTTTGTAGGATA
TTCTATTTTCTGACGAGTAACAAAGTTTGG
GATGAACATAATAAGCAATGACGGCAGCAA
ATTTAACCGAAGATTATTTCGATTTTCTGC
GATGAACATAATAAGCAATGAAGGCAGCAA
TTAACCGAAGATGATTTCGATTTTCTGACG
CGTTGAGGCTTGCGTTTATGGGACGCCGGC
GTTTGGATTGCTACTGACCGCTCTCGGGCT
ATTGCTACTGACCGCTCTCGTGCTCGTCAC
TTGTAGGATACCCTCGCTTTCCTGCTCCTG
TTATTGCTGCCGTCATTGCTTATTATGTTC
ATTTAACCGAAGATGATTTCGCTTTTCTGA
GATGAACATAATAAGCAATGACGGCAGCAA
GATGAACATAATAAGCAATGACGGCAGCAA
GCGTTGAGGCTTGCGGTTATGGTACGCTGG
AAGCTCATTCAGGCTTCTGCCGTTTTGGAT
TTTAACCGAAGATGCTTTCGATTTTCTGAC
GATGAACATAATAAGCAATGACGGCAGCAA
GATGAACA

GCGTTGAGGCTTGCGTTTATGGGACGCCGG
CCTCGCTTTCCTGCTCCTGTTGAGTTTATT
CGCTCTCGTTCTCGTCGCTGCGTTGAGGCT
TTGCTACTGACCGCTCTCGTGCTCGGCGCT
GCTGCGTTGAGGCTTGCGTTTATGGTAAGC
TCCATGATGAGACAGGCCGTTTGAATGTTG
ACTTTGTAGGATACCCCCGCTTTCCTGCTC
CTGCGTTGAGGCTTGCGGTTTTGGTAGGCT
TCTGACGAGTAACAAAGTTTCGATTGCTAC
ACGCTGGACTTTGTAGGATACCCTCGCTTT
TTCCATGATGAGACAGGCCGTTTGAATGTT
TTCCATGATGAGACAGGCCGTTTGAATGTT
ACGAGTAACAAAGATTGGATTGCTACTGAC
AGTTTGGATTGCTACTGACCGCTCTCGTGC
TCCCCGATGAGACAGGCCGCTTTAATGTTT
ACATAGTTTGGATTGCTACTGACCGCTCTC
TTCAGGCGTTTCGATATTTTTCAATGGAAG
TTCCATGATGAGACAGGCCGGTTGAATGTT
TTCCATGATGAGACAGGCCGTTTGAATGTT
GTTTTTGGTACGCTGGACTTTGTTGGATAC
TTCTCTGATGAGACAGGCCGATTGAATGTT
CCATGATGAGACAGCCCGCTTTCATGTTCA
TCCCATGATGAAAAAGGCCACTTCCATGTT
TTCCATGATGAGAAAGGCCGTTTGAATGTT
CGCTCTCGTGCTCGTCGCTGCGTTGAGACT
TTCCATGATGAGACAGGCCGTTTGAATGTT
CTTCCATGATGAGACAGGCCGTTTGAATGT
ATGGTACGCTGGGCTTTGTAGGATACCCCC
CTTATTATGTTCATCCCGTCAACATTCAAA
TGGGACGCTGGACTTTTTAGGATACACTCG
TGCGTTGAGGCTTGCGTTTATGGTACGCTG
CTGACGAGTAACAAAGCTTGGATTGCTACT
AACCTCGC

In [178]:
# find reads containing overlaps - only 1 read - will put it in a loop next
## Includes building the dictionary 

def overlap_all_pairs(read_list, kmer_length):
    # initalize variables
    reads_with_overlaps = 0
    kmer_dict = defaultdict(set)
    pairs = []
    
    # build the dictionary
    for r in read_list: 
        for i in range(len(r)+1): 
            substring = r[i:i+kmer_length]
            if len(substring) == kmer_length: 
                kmer_dict[substring].add(r)
        
    #find overlaps
    for r in read_list:
        overlap_found = False
        suffix = r[-kmer_length:]
        possibilities = kmer_dict[suffix]
        for p in possibilities: 
            if p != r:  
                pair_overlap  = overlap(r,p,kmer_length)
                if pair_overlap > 0: 
                    pairs.append((r,p))
                    overlap_found = True
        if overlap_found == True: 
            reads_with_overlaps +=1
    print("Number of kmers in dictionary: " + str(len(kmer_dict)))
    print(kmer_dict)
    print("Number of pairs: " + str(len(pairs)))
    print(pairs)
    print(reads_with_overlaps)
    return len(pairs), reads_with_overlaps

In [170]:
reads = ['ABCDEFG', 'EFGHIJ', 'HIJABC']
overlap_all_pairs(reads,3)

Number of kmers in dictionary: 10
defaultdict(<class 'set'>, {'ABC': {'HIJABC', 'ABCDEFG'}, 'BCD': {'ABCDEFG'}, 'CDE': {'ABCDEFG'}, 'DEF': {'ABCDEFG'}, 'EFG': {'EFGHIJ', 'ABCDEFG'}, 'FGH': {'EFGHIJ'}, 'GHI': {'EFGHIJ'}, 'HIJ': {'HIJABC', 'EFGHIJ'}, 'IJA': {'HIJABC'}, 'JAB': {'HIJABC'}})
Number of pairs: 3
[('ABCDEFG', 'EFGHIJ'), ('EFGHIJ', 'HIJABC'), ('HIJABC', 'ABCDEFG')]
3


3

In [172]:
overlap_all_pairs(reads,4)

Number of kmers in dictionary: 10
defaultdict(<class 'set'>, {'ABCD': {'ABCDEFG'}, 'BCDE': {'ABCDEFG'}, 'CDEF': {'ABCDEFG'}, 'DEFG': {'ABCDEFG'}, 'EFGH': {'EFGHIJ'}, 'FGHI': {'EFGHIJ'}, 'GHIJ': {'EFGHIJ'}, 'HIJA': {'HIJABC'}, 'IJAB': {'HIJABC'}, 'JABC': {'HIJABC'}})
Number of pairs: 0
[]
0


0

In [173]:
reads = ['CGTACG', 'TACGTA', 'GTACGT', 'ACGTAC', 'GTACGA', 'TACGAT']
overlap_all_pairs(reads, 4)

Number of kmers in dictionary: 6
defaultdict(<class 'set'>, {'CGTA': {'CGTACG', 'ACGTAC', 'TACGTA'}, 'GTAC': {'GTACGT', 'CGTACG', 'GTACGA', 'ACGTAC'}, 'TACG': {'CGTACG', 'GTACGA', 'TACGAT', 'TACGTA', 'GTACGT'}, 'ACGT': {'GTACGT', 'ACGTAC', 'TACGTA'}, 'ACGA': {'TACGAT', 'GTACGA'}, 'CGAT': {'TACGAT'}})
Number of pairs: 12
[('CGTACG', 'GTACGA'), ('CGTACG', 'TACGAT'), ('CGTACG', 'TACGTA'), ('CGTACG', 'GTACGT'), ('TACGTA', 'CGTACG'), ('TACGTA', 'ACGTAC'), ('GTACGT', 'ACGTAC'), ('GTACGT', 'TACGTA'), ('ACGTAC', 'GTACGT'), ('ACGTAC', 'CGTACG'), ('ACGTAC', 'GTACGA'), ('GTACGA', 'TACGAT')]
12


12

In [174]:
overlap_all_pairs(reads, 5)

Number of kmers in dictionary: 6
defaultdict(<class 'set'>, {'CGTAC': {'CGTACG', 'ACGTAC'}, 'GTACG': {'GTACGT', 'CGTACG', 'GTACGA'}, 'TACGT': {'GTACGT', 'TACGTA'}, 'ACGTA': {'ACGTAC', 'TACGTA'}, 'TACGA': {'TACGAT', 'GTACGA'}, 'ACGAT': {'TACGAT'}})
Number of pairs: 6
[('CGTACG', 'GTACGT'), ('CGTACG', 'GTACGA'), ('TACGTA', 'ACGTAC'), ('GTACGT', 'TACGTA'), ('ACGTAC', 'CGTACG'), ('GTACGA', 'TACGAT')]
6


6

In [179]:
overlap_all_pairs(seqs,30)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



(904746, 7161)

Number of pairs: 904746
Reads with pairs: 7161